### Automated Feature Engineering 
Feature engineering is an iterative process involving testing, adjusting, and refining new features.
In this notebook we are practising FeatureTool for the Automated Feature Engineering.

The data used is :Data from Home Credit Default Risk competition from Kaggle.
Objective of this notebook is to:

1) Get familiarise with FeatureTools and to understand how it helps in Modeling. 

2) Which are the most influencial feature in determining credit default.

3) What are the ways of verifying features generated with FeatureTools.


#### There are basically 7 different sources of data:

1.application_train/application_test: the main training and testing data with information about each loan application at Home Credit. Every loan has its own row and is identified by the feature SK_ID_CURR. The training application data comes with the TARGET indicating 0: the loan was repaid or 1: the loan was not repaid.

2.bureau: data concerning client's previous credits from other financial institutions. Each previous credit has its own row in bureau, but one loan in the application data can have multiple previous credits.

3.bureau_balance: monthly data about the previous credits in bureau. Each row is one month of a previous credit, and a single previous credit can have multiple rows, one for each month of the credit length.

4.previous_application: previous applications for loans at Home Credit of clients who have loans in the application data. Each current loan in the application data can have multiple previous loans. Each previous application has one row and is identified by the feature SK_ID_PREV.

5.POS_CASH_BALANCE: monthly data about previous point of sale or cash loans clients have had with Home Credit. Each row is one month of a previous point of sale or cash loan, and a single previous loan can have many rows.

6.credit_card_balance: monthly data about previous credit cards clients have had with Home Credit. Each row is one month of a credit card balance, and a single credit card can have many rows.

7.installments_payment: payment history for previous loans at Home Credit. There is one row for every made payment and one row for every missed payment.

Also another file is provided with the entire column definition : HomeCredit_columns_description.csv 

In [1]:
# Imports

# numpy and pandas for data manipulation
import numpy as np
import pandas as pd 

# File system manangement
import os

# Suppress warnings 
import warnings
warnings.filterwarnings('ignore')

# matplotlib and seaborn for plotting
import matplotlib.pyplot as plt
import seaborn as sns

# import Featuretools
import featuretools as ft

#### Read in Data and Create Small Datasets

We will read in the full dataset, sort by the SK_ID_CURR and keep only the first 1000 rows to make the calculations feasible. Later we can convert to a script and run with the entire datasets.

In [36]:
# Read in the datasets and limit to the first 1000 rows (sorted by SK_ID_CURR) 
# This allows us to actually see the results in a reasonable amount of time! 
app_train = pd.read_csv('../input/application_train.csv').sort_values('SK_ID_CURR').reset_index(drop = True) 
app_test = pd.read_csv('../input/application_test.csv').sort_values('SK_ID_CURR').reset_index(drop = True) 
bureau = pd.read_csv('../input/bureau.csv').sort_values(['SK_ID_CURR', 'SK_ID_BUREAU']).reset_index(drop = True) 
bureau_balance = pd.read_csv('../input/bureau_balance.csv').sort_values('SK_ID_BUREAU').reset_index(drop = True) 
cash = pd.read_csv('../input/POS_CASH_balance.csv').sort_values(['SK_ID_CURR', 'SK_ID_PREV']).reset_index(drop = True) 
credit = pd.read_csv('../input/credit_card_balance.csv').sort_values(['SK_ID_CURR', 'SK_ID_PREV']).reset_index(drop = True)  
previous = pd.read_csv('../input/previous_application.csv').sort_values(['SK_ID_CURR', 'SK_ID_PREV']).reset_index(drop = True) 
installments = pd.read_csv('../input/installments_payments.csv').sort_values(['SK_ID_CURR', 'SK_ID_PREV']).reset_index(drop = True) 

#### Featuretools Basics
Featuretools is an open-source Python library for automatically creating features out of a set of related tables using a technique called deep feature synthesis. Automated feature engineering, like many topics in machine learning, is a complex subject built upon a foundation of simpler ideas. By going through these ideas one at a time, we can build up our understanding of how featuretools which will later allow for us to get the most out of it.

There are a few concepts that we will cover along the way:

Entities and EntitySets

Relationships between tables

Feature primitives: aggregations and transformations

Deep feature synthesis


Entities and Entitysets

An entity is simply a table or in Pandas, a dataframe. The observations are in the rows and the features in the columns. An entity in featuretools must have a unique index where none of the elements are duplicated. 

An EntitySet is a collection of tables and the relationships between them. This can be thought of a data structute with its own methods and attributes. Using an EntitySet allows us to group together multiple tables and manipulate them much quicker than individual tables.

First we'll make an empty entityset named clients to keep track of all the data.

In [37]:
# Entity set with id applications
es = ft.EntitySet(id = 'clients')

In [38]:
# Entities with a unique index
es = es.entity_from_dataframe(entity_id = 'app', dataframe = app_train, index = 'SK_ID_CURR')

es = es.entity_from_dataframe(entity_id = 'bureau', dataframe = bureau, index = 'SK_ID_BUREAU')

es = es.entity_from_dataframe(entity_id = 'previous', dataframe = previous, index = 'SK_ID_PREV')

# Entities that do not have a unique index
es = es.entity_from_dataframe(entity_id = 'bureau_balance', dataframe = bureau_balance, 
                              make_index = True, index = 'bureaubalance_index')

es = es.entity_from_dataframe(entity_id = 'cash', dataframe = cash, 
                              make_index = True, index = 'cash_index')

es = es.entity_from_dataframe(entity_id = 'installments', dataframe = installments,
                              make_index = True, index = 'installments_index')

es = es.entity_from_dataframe(entity_id = 'credit', dataframe = credit,
                              make_index = True, index = 'credit_index')

In [39]:
es

Entityset: clients
  Entities:
    app [Rows: 1001, Columns: 122]
    bureau [Rows: 1001, Columns: 17]
    previous [Rows: 1001, Columns: 37]
    bureau_balance [Rows: 1001, Columns: 4]
    cash [Rows: 1001, Columns: 9]
    installments [Rows: 1001, Columns: 9]
    credit [Rows: 1001, Columns: 24]
  Relationships:
    No relationships

In [40]:
bureau.head()

SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY  DAYS_CREDIT  \
0      100001       5896630        Closed      currency 1         -857   
1      100001       5896631        Closed      currency 1         -909   
2      100001       5896632        Closed      currency 1         -879   
3      100001       5896633        Closed      currency 1        -1572   
4      100001       5896634        Active      currency 1         -559   

   CREDIT_DAY_OVERDUE  DAYS_CREDIT_ENDDATE  DAYS_ENDDATE_FACT  \
0                   0               -492.0             -553.0   
1                   0               -179.0             -877.0   
2                   0               -514.0             -544.0   
3                   0              -1329.0            -1328.0   
4                   0                902.0                NaN   

   AMT_CREDIT_MAX_OVERDUE  CNT_CREDIT_PROLONG  AMT_CREDIT_SUM  \
0                     NaN                   0        112500.0   
1                     NaN                   0        279720.0   
2                     NaN                   0         91620.0   
3                     NaN                   0         85500.0   
4                     NaN                   0        337680.0   

   AMT_CREDIT_SUM_DEBT  AMT_CREDIT_SUM_LIMIT  AMT_CREDIT_SUM_OVERDUE  \
0                  0.0                   0.0                     0.0   
1                  0.0                   0.0                     0.0   
2                  0.0                   0.0                     0.0   
3                  0.0                   0.0                     0.0   
4             113166.0                   0.0                     0.0   

       CREDIT_TYPE  DAYS_CREDIT_UPDATE  AMT_ANNUITY  
0  Consumer credit                -155          0.0  
1  Consumer credit                -155          0.0  
2  Consumer credit                -155          0.0  
3  Consumer credit                -155          0.0  
4  Consumer credit                  -6       4630.5

In [41]:
print('Parent: app_train, Parent Variable: SK_ID_CURR\n\n', app_train.iloc[:, 111:115].head())
print('\nChild: bureau, Child Variable: SK_ID_CURR\n\n', bureau.iloc[10:30, :4].head())

Parent: app_train, Parent Variable: SK_ID_CURR

    FLAG_DOCUMENT_17  FLAG_DOCUMENT_18  FLAG_DOCUMENT_19  FLAG_DOCUMENT_20
0                 0                 0                 0                 0
1                 0                 0                 0                 0
2                 0                 0                 0                 0
3                 0                 0                 0                 0
4                 0                 0                 0                 0

Child: bureau, Child Variable: SK_ID_CURR

     SK_ID_CURR  SK_ID_BUREAU CREDIT_ACTIVE CREDIT_CURRENCY
10      100002       6158905        Closed      currency 1
11      100002       6158906        Closed      currency 1
12      100002       6158907        Closed      currency 1
13      100002       6158908        Closed      currency 1
14      100002       6158909        Active      currency 1


Lets Identify the relationship betwenn the df's

In [42]:
# Relationship between app and bureau
r_app_bureau = ft.Relationship(es['app']['SK_ID_CURR'], es['bureau']['SK_ID_CURR'])

# Relationship between bureau and bureau balance
r_bureau_balance = ft.Relationship(es['bureau']['SK_ID_BUREAU'], es['bureau_balance']['SK_ID_BUREAU'])

# Relationship between current app and previous apps
r_app_previous = ft.Relationship(es['app']['SK_ID_CURR'], es['previous']['SK_ID_CURR'])

# Relationships between previous apps and cash, installments, and credit
r_previous_cash = ft.Relationship(es['previous']['SK_ID_PREV'], es['cash']['SK_ID_PREV'])
r_previous_installments = ft.Relationship(es['previous']['SK_ID_PREV'], es['installments']['SK_ID_PREV'])
r_previous_credit = ft.Relationship(es['previous']['SK_ID_PREV'], es['credit']['SK_ID_PREV'])

In [43]:
r_app_previous.parent_entity

Entity: app
  Variables:
    SK_ID_CURR (dtype: index)
    TARGET (dtype: numeric)
    NAME_CONTRACT_TYPE (dtype: categorical)
    CODE_GENDER (dtype: categorical)
    FLAG_OWN_CAR (dtype: categorical)
    FLAG_OWN_REALTY (dtype: categorical)
    CNT_CHILDREN (dtype: numeric)
    AMT_INCOME_TOTAL (dtype: numeric)
    AMT_CREDIT (dtype: numeric)
    AMT_ANNUITY (dtype: numeric)
    AMT_GOODS_PRICE (dtype: numeric)
    NAME_TYPE_SUITE (dtype: categorical)
    NAME_INCOME_TYPE (dtype: categorical)
    NAME_EDUCATION_TYPE (dtype: categorical)
    NAME_FAMILY_STATUS (dtype: categorical)
    NAME_HOUSING_TYPE (dtype: categorical)
    REGION_POPULATION_RELATIVE (dtype: numeric)
    DAYS_BIRTH (dtype: numeric)
    DAYS_EMPLOYED (dtype: numeric)
    DAYS_REGISTRATION (dtype: numeric)
    DAYS_ID_PUBLISH (dtype: numeric)
    OWN_CAR_AGE (dtype: numeric)
    FLAG_MOBIL (dtype: numeric)
    FLAG_EMP_PHONE (dtype: numeric)
    FLAG_WORK_PHONE (dtype: numeric)
    FLAG_CONT_MOBILE (dtype: numeric)
 

In [44]:
# Add in the defined relationships
es = es.add_relationships([r_app_bureau, r_bureau_balance, r_app_previous,
                           r_previous_cash, r_previous_installments, r_previous_credit])
# Print out the EntitySet
es

Entityset: clients
  Entities:
    app [Rows: 1001, Columns: 122]
    bureau [Rows: 1001, Columns: 17]
    previous [Rows: 1001, Columns: 37]
    bureau_balance [Rows: 1001, Columns: 4]
    cash [Rows: 1001, Columns: 9]
    installments [Rows: 1001, Columns: 9]
    credit [Rows: 1001, Columns: 24]
  Relationships:
    bureau.SK_ID_CURR -> app.SK_ID_CURR
    bureau_balance.SK_ID_BUREAU -> bureau.SK_ID_BUREAU
    previous.SK_ID_CURR -> app.SK_ID_CURR
    cash.SK_ID_PREV -> previous.SK_ID_PREV
    installments.SK_ID_PREV -> previous.SK_ID_PREV
    credit.SK_ID_PREV -> previous.SK_ID_PREV

Feature Primitives

A feature primitive is an operation applied to a table or a set of tables to create a feature. These represent simple calculations, many of which we already use in manual feature engineering, that can be stacked on top of each other to create complex features. Feature primitives fall into two categories:

Aggregation: function that groups together child datapoints for each parent and then calculates a statistic such as mean, min, max, or standard deviation. An example is calculating the maximum previous loan amount for each client. An aggregation works across multiple tables using relationships between tables.

Transformation: an operation applied to one or more columns in a single table. An example would be taking the absolute value of a column, or finding the difference between two columns in one table.
A list of the available features primitives in featuretools can be viewed below.

In [45]:
# List the primitives in a dataframe
primitives = ft.list_primitives()
pd.options.display.max_colwidth = 100
primitives[primitives['type'] == 'aggregation'].head(10)

name         type  \
0             last  aggregation   
1             mean  aggregation   
2     percent_true  aggregation   
3  time_since_last  aggregation   
4            count  aggregation   
5    n_most_common  aggregation   
6         num_true  aggregation   
7              all  aggregation   
8             mode  aggregation   
9              any  aggregation   

                                                  description  
0                                     Returns the last value.  
1            Computes the average value of a numeric feature.  
2    Finds the percent of 'True' values in a boolean feature.  
3                           Time since last related instance.  
4                       Counts the number of non null values.  
5  Finds the N most common elements in a categorical feature.  
6             Finds the number of 'True' values in a boolean.  
7                              Test if all values are 'True'.  
8     Finds the most common element in a categorical feature.  
9                                Test if any value is 'True'.

In [46]:
primitives[primitives['type'] == 'transform'].head(10)

name       type  \
19      minute  transform   
20      second  transform   
21       hours  transform   
22   cum_count  transform   
23    multiply  transform   
24         add  transform   
25         day  transform   
26         and  transform   
27  days_since  transform   
28   longitude  transform   

                                                                                           description  
19                                                       Transform a Datetime feature into the minute.  
20                                                       Transform a Datetime feature into the second.  
21                                             Transform a Timedelta feature into the number of hours.  
22  Calculates the number of previous values of an instance for each value in a time-dependent entity.  
23                                            Creates a transform feature that multplies two features.  
24                                                 Creates a transform feature that adds two features.  
25                                                          Transform a Datetime feature into the day.  
26                                        For two boolean values, determine if both values are 'True'.  
27                           For each value of the base feature, compute the number of days between it  
28                                                 Returns the second value on the tuple base feature.

Deep Feature Synthesis

Deep Feature Synthesis (DFS) is the process featuretools uses to make new features. DFS stacks feature primitives to form features with a "depth" equal to the number of primitives. 

To perform DFS in featuretools, we use the dfs function passing it an entityset, the target_entity (where we want to make the features), the agg_primitives to use, the trans_primitives to use and the max_depth of the features. Here we will use the default aggregation and transformation primitives, a max depth of 2, and calculate primitives for the app entity. Because this process is computationally expensive, we can run the function using features_only = True to return only a list of the features and not calculate the features themselves. This can be useful to look at the resulting features before starting an extended computation.

In [47]:
# Default primitives from featuretools
default_agg_primitives =  ["sum", "std", "max", "skew", "min", "mean", "count", "percent_true", "num_unique", "mode"]
default_trans_primitives =  ["day", "year", "month", "weekday", "haversine", "numwords", "characters"]

# DFS with specified primitives
feature_names = ft.dfs(entityset = es, target_entity = 'app',
                       trans_primitives = default_trans_primitives,
                       agg_primitives=default_agg_primitives, 
                       max_depth = 2, features_only=True)

print('%d Total Features' % len(feature_names))

1696 Total Features


In [48]:
# DFS with default primitives
feature_matrix, feature_names = ft.dfs(entityset = es, target_entity = 'app',
                                       trans_primitives = default_trans_primitives,
                                       agg_primitives=default_agg_primitives, 
                                        max_depth = 2, features_only=False, verbose = True)

pd.options.display.max_columns = 1700
feature_matrix.head(10)

Built 1696 features
Elapsed: 00:27 | Remaining: 00:00 | Progress: 100%|██████████████████████████████████████████| Calculated: 11/11 chunks


TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
SK_ID_CURR                                                       
100002           1         Cash loans           M            N   
100003           0         Cash loans           F            N   
100004           0    Revolving loans           M            Y   
100006           0         Cash loans           F            N   
100007           0         Cash loans           M            N   
100008           0         Cash loans           M            N   
100009           0         Cash loans           F            Y   
100010           0         Cash loans           M            Y   
100011           0         Cash loans           F            N   
100012           0    Revolving loans           M            N   

           FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR                                                               
100002                   Y             0          202500.0    406597.5   
100003                   N             0          270000.0   1293502.5   
100004                   Y             0           67500.0    135000.0   
100006                   Y             0          135000.0    312682.5   
100007                   Y             0          121500.0    513000.0   
100008                   Y             0           99000.0    490495.5   
100009                   Y             1          171000.0   1560726.0   
100010                   Y             0          360000.0   1530000.0   
100011                   Y             0          112500.0   1019610.0   
100012                   Y             0          135000.0    405000.0   

            AMT_ANNUITY  AMT_GOODS_PRICE  NAME_TYPE_SUITE  \
SK_ID_CURR                                                  
100002          24700.5         351000.0    Unaccompanied   
100003          35698.5        1129500.0           Family   
100004           6750.0         135000.0    Unaccompanied   
100006          29686.5         297000.0    Unaccompanied   
100007          21865.5         513000.0    Unaccompanied   
100008          27517.5         454500.0  Spouse, partner   
100009          41301.0        1395000.0    Unaccompanied   
100010          42075.0        1530000.0    Unaccompanied   
100011          33826.5         913500.0         Children   
100012          20250.0         405000.0    Unaccompanied   

                NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
SK_ID_CURR                                                        
100002                   Working  Secondary / secondary special   
100003             State servant               Higher education   
100004                   Working  Secondary / secondary special   
100006                   Working  Secondary / secondary special   
100007                   Working  Secondary / secondary special   
100008             State servant  Secondary / secondary special   
100009      Commercial associate               Higher education   
100010             State servant               Higher education   
100011                 Pensioner  Secondary / secondary special   
100012                   Working  Secondary / secondary special   

              NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
SK_ID_CURR                                            
100002      Single / not married  House / apartment   
100003                   Married  House / apartment   
100004      Single / not married  House / apartment   
100006            Civil marriage  House / apartment   
100007      Single / not married  House / apartment   
100008                   Married  House / apartment   
100009                   Married  House / apartment   
100010                   Married  House / apartment   
100011                   Married  House / apartment   
100012      Single / not married  House / apartment   

            REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
SK_ID_CURR                                                    

In [49]:
feature_names[-20:]

[<Feature: SKEW(bureau.MEAN(bureau_balance.MONTHS_BALANCE))>,
 <Feature: SKEW(bureau.COUNT(bureau_balance))>,
 <Feature: SKEW(bureau.NUM_UNIQUE(bureau_balance.STATUS))>,
 <Feature: MIN(bureau.SUM(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MIN(bureau.STD(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MIN(bureau.MAX(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MIN(bureau.SKEW(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MIN(bureau.MEAN(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MIN(bureau.COUNT(bureau_balance))>,
 <Feature: MIN(bureau.NUM_UNIQUE(bureau_balance.STATUS))>,
 <Feature: MEAN(bureau.SUM(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MEAN(bureau.STD(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MEAN(bureau.MAX(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MEAN(bureau.SKEW(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MEAN(bureau.MIN(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MEAN(bureau.MEAN(bureau_balance.MONTHS_BALANCE))>,
 <Feature: MEAN(bureau.COUNT(bureau_balance))>,
 <Feat

Lets specify a smaller set of features to reduce the curse of dimensionality. 
We still are not using much domain knowledge, but this feature set will be more manageable. The next step from here is improving the features we actually build and performing feature selection.

In [50]:
# Specify the aggregation primitives
feature_matrix_spec, feature_names_spec = ft.dfs(entityset = es, target_entity = 'app',  
                                                 agg_primitives = ['sum', 'count', 'min', 'max', 'mean', 'mode'], 
                                                 max_depth = 2, features_only = False, verbose = True)

Built 883 features
Elapsed: 00:11 | Remaining: 00:00 | Progress: 100%|██████████████████████████████████████████| Calculated: 11/11 chunks


In [52]:
pd.options.display.max_columns = 1000
feature_matrix_spec.head(10)

TARGET NAME_CONTRACT_TYPE CODE_GENDER FLAG_OWN_CAR  \
SK_ID_CURR                                                       
100002           1         Cash loans           M            N   
100003           0         Cash loans           F            N   
100004           0    Revolving loans           M            Y   
100006           0         Cash loans           F            N   
100007           0         Cash loans           M            N   
100008           0         Cash loans           M            N   
100009           0         Cash loans           F            Y   
100010           0         Cash loans           M            Y   
100011           0         Cash loans           F            N   
100012           0    Revolving loans           M            N   

           FLAG_OWN_REALTY  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
SK_ID_CURR                                                               
100002                   Y             0          202500.0    406597.5   
100003                   N             0          270000.0   1293502.5   
100004                   Y             0           67500.0    135000.0   
100006                   Y             0          135000.0    312682.5   
100007                   Y             0          121500.0    513000.0   
100008                   Y             0           99000.0    490495.5   
100009                   Y             1          171000.0   1560726.0   
100010                   Y             0          360000.0   1530000.0   
100011                   Y             0          112500.0   1019610.0   
100012                   Y             0          135000.0    405000.0   

            AMT_ANNUITY  AMT_GOODS_PRICE  NAME_TYPE_SUITE  \
SK_ID_CURR                                                  
100002          24700.5         351000.0    Unaccompanied   
100003          35698.5        1129500.0           Family   
100004           6750.0         135000.0    Unaccompanied   
100006          29686.5         297000.0    Unaccompanied   
100007          21865.5         513000.0    Unaccompanied   
100008          27517.5         454500.0  Spouse, partner   
100009          41301.0        1395000.0    Unaccompanied   
100010          42075.0        1530000.0    Unaccompanied   
100011          33826.5         913500.0         Children   
100012          20250.0         405000.0    Unaccompanied   

                NAME_INCOME_TYPE            NAME_EDUCATION_TYPE  \
SK_ID_CURR                                                        
100002                   Working  Secondary / secondary special   
100003             State servant               Higher education   
100004                   Working  Secondary / secondary special   
100006                   Working  Secondary / secondary special   
100007                   Working  Secondary / secondary special   
100008             State servant  Secondary / secondary special   
100009      Commercial associate               Higher education   
100010             State servant               Higher education   
100011                 Pensioner  Secondary / secondary special   
100012                   Working  Secondary / secondary special   

              NAME_FAMILY_STATUS  NAME_HOUSING_TYPE  \
SK_ID_CURR                                            
100002      Single / not married  House / apartment   
100003                   Married  House / apartment   
100004      Single / not married  House / apartment   
100006            Civil marriage  House / apartment   
100007      Single / not married  House / apartment   
100008                   Married  House / apartment   
100009                   Married  House / apartment   
100010                   Married  House / apartment   
100011                   Married  House / apartment   
100012      Single / not married  House / apartment   

            REGION_POPULATION_RELATIVE  DAYS_BIRTH  DAYS_EMPLOYED  \
SK_ID_CURR                                                    

So from this we can see that within few lines of code, we have generated 883 features from 121 initial features. The amount of time it saves while having a baseline is remarkable and hence its picking up its popularity among the Automated Feature Engineering Techniques.

#### How to assess the fetaure performance?

To determine whether our basic implementation of featuretools was useful, we can look at several results:

1.Cross validation scores 

2.Correlations: both between the features and the TARGET, and between features themselves

3.Feature importances: determined by a gradient boosting machine model

#### Correlations

Now we can look at correlations within the data.Using correlations is fine as a first approximation for identifying "good features", but it is not a rigorous feature selection method.If there are very highly correlated varibables, we might want to think about removing some of them to reduce the effect of collinearity between features.

In [53]:
feature_matrix_spec_corr = feature_matrix_spec.corr(method='pearson', min_periods=1)

In [54]:
feature_matrix_spec_corr.head()

TARGET  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
TARGET            1.000000      0.025307         -0.007118    0.008316   
CNT_CHILDREN      0.025307      1.000000          0.056153    0.036706   
AMT_INCOME_TOTAL -0.007118      0.056153          1.000000    0.429200   
AMT_CREDIT        0.008316      0.036706          0.429200    1.000000   
AMT_ANNUITY       0.024608      0.055900          0.491201    0.797082   

                  AMT_ANNUITY  AMT_GOODS_PRICE  REGION_POPULATION_RELATIVE  \
TARGET               0.024608        -0.001968                    0.014177   
CNT_CHILDREN         0.055900         0.035616                   -0.059956   
AMT_INCOME_TOTAL     0.491201         0.439771                    0.184463   
AMT_CREDIT           0.797082         0.986030                    0.074188   
AMT_ANNUITY          1.000000         0.798889                    0.106804   

                  DAYS_BIRTH  DAYS_EMPLOYED  DAYS_REGISTRATION  \
TARGET              0.082907      -0.010218           0.017294   
CNT_CHILDREN        0.304262      -0.219229           0.210907   
AMT_INCOME_TOTAL    0.089231      -0.208930           0.130151   
AMT_CREDIT         -0.065376      -0.115705           0.028113   
AMT_ANNUITY         0.019999      -0.139575           0.058741   

                  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  FLAG_EMP_PHONE  \
TARGET                   0.055585    -0.042166         NaN        0.011991   
CNT_CHILDREN            -0.036245     0.094183         NaN        0.220268   
AMT_INCOME_TOTAL         0.046033    -0.245352         NaN        0.208312   
AMT_CREDIT              -0.023237    -0.126970         NaN        0.113665   
AMT_ANNUITY             -0.023620    -0.123864         NaN        0.138311   

                  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL  \
TARGET                   0.049613          0.015034   -0.015172   -0.007614   
CNT_CHILDREN             0.020615          0.005554   -0.038205    0.034589   
AMT_INCOME_TOTAL        -0.063976          0.032639   -0.029274    0.094235   
AMT_CREDIT              -0.060961          0.062921    0.018226    0.052418   
AMT_ANNUITY             -0.078152          0.075392   -0.014300    0.102624   

                  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
TARGET                  -0.004360              0.048279   
CNT_CHILDREN             0.878877              0.002747   
AMT_INCOME_TOTAL         0.056320             -0.241708   
AMT_CREDIT               0.107518             -0.112283   
AMT_ANNUITY              0.115235             -0.176090   

                  REGION_RATING_CLIENT_W_CITY  HOUR_APPR_PROCESS_START  \
TARGET                               0.047879                -0.047849   
CNT_CHILDREN                         0.004397                -0.027266   
AMT_INCOME_TOTAL                    -0.255260                 0.068345   
AMT_CREDIT                          -0.114617                 0.024222   
AMT_ANNUITY                         -0.176450                 0.053840   

                  REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
TARGET                              0.051329                    0.034044   
CNT_CHILDREN                        0.017909                   -0.000718   
AMT_INCOME_TOTAL                    0.077169                    0.155852   
AMT_CREDIT                          0.015075                    0.006847   
AMT_ANNUITY                         0.036977                    0.073958   

                  LIVE_REGION_NOT_WORK_REGION  REG_CITY_NOT_LIVE_CITY  \
TARGET                               0.035034                0.015907   
CNT_CHILDREN                        -0.008461                0.024903   
AMT_INCOME_TOTAL                     0.135045                0.006380   
AMT_CREDIT                           0.004391               -0.009515   
AMT_ANNUITY                          0.075531                0.022481   

                  REG_CITY_NOT_WORK_CITY  LIVE_CITY_NOT_WORK_CITY  \


In [55]:
feature_matrix_spec_corr.to_csv('correlation_spec.csv')

In [56]:
correlations = pd.read_csv('../input/correlation_spec.csv',index_col = 0)

In [57]:
correlations.index.name = 'Variable'
correlations.head()

TARGET  CNT_CHILDREN  AMT_INCOME_TOTAL  AMT_CREDIT  \
Variable                                                                 
TARGET            1.000000      0.025307         -0.007118    0.008316   
CNT_CHILDREN      0.025307      1.000000          0.056153    0.036706   
AMT_INCOME_TOTAL -0.007118      0.056153          1.000000    0.429200   
AMT_CREDIT        0.008316      0.036706          0.429200    1.000000   
AMT_ANNUITY       0.024608      0.055900          0.491201    0.797082   

                  AMT_ANNUITY  AMT_GOODS_PRICE  REGION_POPULATION_RELATIVE  \
Variable                                                                     
TARGET               0.024608        -0.001968                    0.014177   
CNT_CHILDREN         0.055900         0.035616                   -0.059956   
AMT_INCOME_TOTAL     0.491201         0.439771                    0.184463   
AMT_CREDIT           0.797082         0.986030                    0.074188   
AMT_ANNUITY          1.000000         0.798889                    0.106804   

                  DAYS_BIRTH  DAYS_EMPLOYED  DAYS_REGISTRATION  \
Variable                                                         
TARGET              0.082907      -0.010218           0.017294   
CNT_CHILDREN        0.304262      -0.219229           0.210907   
AMT_INCOME_TOTAL    0.089231      -0.208930           0.130151   
AMT_CREDIT         -0.065376      -0.115705           0.028113   
AMT_ANNUITY         0.019999      -0.139575           0.058741   

                  DAYS_ID_PUBLISH  OWN_CAR_AGE  FLAG_MOBIL  FLAG_EMP_PHONE  \
Variable                                                                     
TARGET                   0.055585    -0.042166         NaN        0.011991   
CNT_CHILDREN            -0.036245     0.094183         NaN        0.220268   
AMT_INCOME_TOTAL         0.046033    -0.245352         NaN        0.208312   
AMT_CREDIT              -0.023237    -0.126970         NaN        0.113665   
AMT_ANNUITY             -0.023620    -0.123864         NaN        0.138311   

                  FLAG_WORK_PHONE  FLAG_CONT_MOBILE  FLAG_PHONE  FLAG_EMAIL  \
Variable                                                                      
TARGET                   0.049613          0.015034   -0.015172   -0.007614   
CNT_CHILDREN             0.020615          0.005554   -0.038205    0.034589   
AMT_INCOME_TOTAL        -0.063976          0.032639   -0.029274    0.094235   
AMT_CREDIT              -0.060961          0.062921    0.018226    0.052418   
AMT_ANNUITY             -0.078152          0.075392   -0.014300    0.102624   

                  CNT_FAM_MEMBERS  REGION_RATING_CLIENT  \
Variable                                                  
TARGET                  -0.004360              0.048279   
CNT_CHILDREN             0.878877              0.002747   
AMT_INCOME_TOTAL         0.056320             -0.241708   
AMT_CREDIT               0.107518             -0.112283   
AMT_ANNUITY              0.115235             -0.176090   

                  REGION_RATING_CLIENT_W_CITY  HOUR_APPR_PROCESS_START  \
Variable                                                                 
TARGET                               0.047879                -0.047849   
CNT_CHILDREN                         0.004397                -0.027266   
AMT_INCOME_TOTAL                    -0.255260                 0.068345   
AMT_CREDIT                          -0.114617                 0.024222   
AMT_ANNUITY                         -0.176450                 0.053840   

                  REG_REGION_NOT_LIVE_REGION  REG_REGION_NOT_WORK_REGION  \
Variable                                                                   
TARGET                              0.051329                    0.034044   
CNT_CHILDREN                        0.017909                   -0.000718   
AMT_INCOME_TOTAL                    0.077169                    0.155852   
AMT_CREDIT                          0.015075                    0.006847   
A

In [66]:
correlations_target = correlations.sort_values('TARGET')['TARGET']
# Most negative correlations
correlations_target.head(10)

Variable
MEAN(previous.MAX(credit.MONTHS_BALANCE))     -0.363774
MAX(credit.MONTHS_BALANCE)                    -0.363774
MIN(previous.MAX(credit.MONTHS_BALANCE))      -0.363774
MEAN(previous.MAX(installments.SK_ID_CURR))   -0.349691
MEAN(previous.MIN(installments.SK_ID_CURR))   -0.349691
MIN(installments.SK_ID_CURR)                  -0.349691
MAX(installments.SK_ID_CURR)                  -0.349691
MAX(previous.MEAN(installments.SK_ID_CURR))   -0.349691
MEAN(installments.SK_ID_CURR)                 -0.349691
MAX(previous.MIN(installments.SK_ID_CURR))    -0.349691
Name: TARGET, dtype: float64

Most negatively correlated features are 

1)Month of balance relative to application date 

2) # of loans 



In [ ]:
# Most positive correlations
correlations_target.dropna().tail()

1) Term of previous credit (can change over time)

2) Installments left to pay on the previous credit

are the most positively correlated 

Here we have seen most correlated fetaures with Target. Need to validate this with other methods as well

Collinear Features

In [59]:
threshold = 0.9

correlated_pairs = {}

# Iterate through the columns
for col in correlations:
    # Find correlations above the threshold
    above_threshold_vars = [x for x in list(correlations.index[correlations[col] > threshold]) if x != col]
    correlated_pairs[col] = above_threshold_vars

In [69]:
correlated_pairs

{'TARGET': [],
 'CNT_CHILDREN': ['MIN(previous.RATE_INTEREST_PRIMARY)',
  'MIN(previous.RATE_INTEREST_PRIVILEGED)',
  'MAX(previous.RATE_INTEREST_PRIMARY)',
  'MAX(previous.RATE_INTEREST_PRIVILEGED)',
  'MEAN(previous.RATE_INTEREST_PRIMARY)',
  'MEAN(previous.RATE_INTEREST_PRIVILEGED)'],
 'AMT_INCOME_TOTAL': [],
 'AMT_CREDIT': ['AMT_GOODS_PRICE'],
 'AMT_ANNUITY': [],
 'AMT_GOODS_PRICE': ['AMT_CREDIT'],
 'REGION_POPULATION_RELATIVE': ['MEAN(credit.AMT_DRAWINGS_POS_CURRENT)',
  'MIN(previous.MEAN(credit.AMT_DRAWINGS_POS_CURRENT))',
  'MAX(previous.MEAN(credit.AMT_DRAWINGS_POS_CURRENT))',
  'MEAN(previous.MEAN(credit.AMT_DRAWINGS_POS_CURRENT))'],
 'DAYS_BIRTH': ['MIN(previous.RATE_INTEREST_PRIMARY)',
  'MIN(previous.RATE_INTEREST_PRIVILEGED)',
  'MAX(previous.RATE_INTEREST_PRIMARY)',
  'MAX(previous.RATE_INTEREST_PRIVILEGED)',
  'MEAN(previous.RATE_INTEREST_PRIMARY)',
  'MEAN(previous.RATE_INTEREST_PRIVILEGED)'],
 'DAYS_EMPLOYED': ['MIN(previous.RATE_INTEREST_PRIMARY)',
  'MIN(previous.RA

In [70]:
correlations['MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT)']

Variable
TARGET                                                   -0.177057
CNT_CHILDREN                                             -0.166484
AMT_INCOME_TOTAL                                         -0.028645
AMT_CREDIT                                               -0.446706
AMT_ANNUITY                                              -0.405153
AMT_GOODS_PRICE                                          -0.479531
REGION_POPULATION_RELATIVE                                0.218748
DAYS_BIRTH                                                0.014368
DAYS_EMPLOYED                                            -0.138249
DAYS_REGISTRATION                                        -0.195092
DAYS_ID_PUBLISH                                           0.001169
OWN_CAR_AGE                                              -0.361362
FLAG_MOBIL                                                     NaN
FLAG_EMP_PHONE                                            0.137933
FLAG_WORK_PHONE                                      

In [71]:
correlated_pairs['MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT)']

['MAX(installments.NUM_INSTALMENT_NUMBER)',
 'MEAN(installments.NUM_INSTALMENT_NUMBER)',
 'MAX(cash.SK_DPD)',
 'MAX(cash.SK_DPD_DEF)',
 'MEAN(cash.CNT_INSTALMENT)',
 'MEAN(cash.SK_DPD)',
 'MEAN(cash.SK_DPD_DEF)',
 'MEAN(credit.AMT_DRAWINGS_CURRENT)',
 'MEAN(credit.AMT_PAYMENT_CURRENT)',
 'SUM(previous.MEAN(credit.AMT_DRAWINGS_CURRENT))',
 'SUM(previous.MEAN(credit.AMT_PAYMENT_CURRENT))',
 'SUM(previous.MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT))',
 'MIN(previous.MAX(installments.NUM_INSTALMENT_NUMBER))',
 'MIN(previous.MEAN(installments.NUM_INSTALMENT_NUMBER))',
 'MIN(previous.MEAN(credit.AMT_DRAWINGS_CURRENT))',
 'MIN(previous.MEAN(credit.AMT_PAYMENT_CURRENT))',
 'MIN(previous.MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT))',
 'MAX(previous.MEAN(installments.NUM_INSTALMENT_NUMBER))',
 'MAX(previous.MIN(cash.CNT_INSTALMENT))',
 'MAX(previous.MEAN(cash.SK_DPD))',
 'MAX(previous.MEAN(cash.SK_DPD_DEF))',
 'MAX(previous.MEAN(credit.AMT_DRAWINGS_CURRENT))',
 'MAX(previous.MEAN(credit.AMT_PAYMENT_CURREN

In [60]:
correlations['MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT)'].sort_values(ascending=False).head()

Variable
MAX(previous.MEAN(cash.SK_DPD))                         1.0
MEAN(previous.MEAN(cash.SK_DPD))                        1.0
MIN(previous.MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT))    1.0
MAX(cash.SK_DPD_DEF)                                    1.0
MEAN(cash.SK_DPD)                                       1.0
Name: MEAN(credit.AMT_PAYMENT_TOTAL_CURRENT), dtype: float64

Remove Low Importance Features

Feature selection is an entire topic by itself, but one thing we can do is remove any features that have only a single unique value or are all null. Featuretools has a default method for doing this available in the selection module.

In [73]:
from featuretools import selection

# Remove features with only one unique value
feature_matrix2 = selection.remove_low_information_features(feature_matrix)

print('Removed %d features' % (feature_matrix.shape[1]- feature_matrix2.shape[1]))

Removed 242 features


So in this section we have understood how Feature tools helps to create more features by Automated Feature Enfgineering using Deep Feature Synthesis.